In [14]:
# Importando Bibliotecas
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
import folium
from folium.plugins import MarkerCluster

In [15]:
df_raw = pd.read_csv('../dataset/zomato.csv')

## Limpando Dados

In [16]:
# Criando Funções:

COUNTRIES = {
1: "India",
14: "Australia",
30: "Brazil",
37: "Canada",
94: "Indonesia",
148: "New Zeland",
162: "Philippines",
166: "Qatar",
184: "Singapure",
189: "South Africa",
191: "Sri Lanka",
208: "Turkey",
214: "United Arab Emirates",
215: "England",
216: "United States of America",
}

def Country_Name(country_id):
    return COUNTRIES[country_id]


# -----------------------------------------------


def create_price_tye(price_range):
    if price_range == 1:
        return "cheap"
    elif price_range == 2:
        return "normal"
    elif price_range == 3:
        return "expensive"
    else:
        return "gourmet"
    
    
# -----------------------------------------------

COLORS = {
"3F7E00": "darkgreen",
"5BA829": "green",
"9ACD32": "lightgreen",
"CDD614": "orange",
"FFBA00": "red",
"CBCBC8": "darkred",
"FF7800": "darkred",
}
def color_name(color_code):
    return COLORS[color_code]

# -----------------------------------------------

def rename_columns(dataframe):
    df1 = dataframe.copy()
    title = lambda x: inflection.titleize(x)
    snakecase = lambda x: inflection.underscore(x)
    spaces = lambda x: x.replace(" ", "")
    cols_old = list(df1.columns)
    cols_old = list(map(title, cols_old))
    cols_old = list(map(spaces, cols_old))
    cols_new = list(map(snakecase, cols_old))
    df1.columns = cols_new
    return df1

In [17]:
df = df_raw.copy()

# Removendo linhas 'NaN'

df = df.dropna(subset=['Restaurant ID'])
df = df.dropna(subset=['Restaurant Name'])
df = df.dropna(subset=['Cuisines'])
df = df.dropna(subset=['Country Code'])
df = df.dropna(subset=['Address'])
df = df.dropna(subset=['Locality'])
df = df.dropna(subset=['Locality Verbose'])
df = df.dropna(subset=['Longitude'])
df = df.dropna(subset=['Average Cost for two'])
df = df.dropna(subset=['Has Table booking'])
df = df.dropna(subset=['Has Online delivery'])
df = df.dropna(subset=['Price range'])
df = df.dropna(subset=['Aggregate rating'])
df = df.dropna(subset=['Rating color'])
df = df.dropna(subset=['Votes'])
df.dropna( )

# Removendo linhas duplicadas
df = df.drop_duplicates().reset_index()

df = df.drop(columns = ['Switch to order menu'], axis=1)

# Define categorias de preço de acordo com o range
df['Price range'] = df['Price range'].apply(create_price_tye)

# Define o padrão de cores das avaliações
df['Rating color'] = df['Rating color'].apply(color_name)

# --------------------------------------------------------

df['Country Name'] = df['Country Code'].map(Country_Name)
# Definisdo os restaurantes po apenas um tipo de culinaria
df["Cuisines"] = df.loc[:, "Cuisines"].astype(str).apply(lambda x: x.split(",")[0])

# df.info() #valores nulos
#print(df.isnull())
# print(df.isna())

In [18]:
# df.info() #valores nulos
#print(df.isnull())
# print(df.isna())
# df = df.drop_duplicates(ignore_index=True)

In [19]:
# df1 = df1.drop('index', axis=1) # Remove index

In [20]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6929 entries, 0 to 6928
Data columns (total 22 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   index                 6929 non-null   int64  
 1   Restaurant ID         6929 non-null   int64  
 2   Restaurant Name       6929 non-null   object 
 3   Country Code          6929 non-null   int64  
 4   City                  6929 non-null   object 
 5   Address               6929 non-null   object 
 6   Locality              6929 non-null   object 
 7   Locality Verbose      6929 non-null   object 
 8   Longitude             6929 non-null   float64
 9   Latitude              6929 non-null   float64
 10  Cuisines              6929 non-null   object 
 11  Average Cost for two  6929 non-null   int64  
 12  Currency              6929 non-null   object 
 13  Has Table booking     6929 non-null   int64  
 14  Has Online delivery   6929 non-null   int64  
 15  Is delivering now    

In [21]:
# pd.set_option('display.max_rows', 30)

## Visão Geral

In [22]:
df1 = df.copy()

### 1. Quantos restaurantes únicos estão registrados?

In [23]:
rest_unique = df1.loc[:, 'Restaurant ID'].nunique()

print(f'Existem {rest_unique} restaurantes únicos registrados')

Existem 6929 restaurantes únicos registrados


In [24]:
df2 = df1['Restaurant ID'].unique()
df2 = pd.DataFrame(df1)
QtdeRest = df2.count()
print(QtdeRest)

index                   6929
Restaurant ID           6929
Restaurant Name         6929
Country Code            6929
City                    6929
Address                 6929
Locality                6929
Locality Verbose        6929
Longitude               6929
Latitude                6929
Cuisines                6929
Average Cost for two    6929
Currency                6929
Has Table booking       6929
Has Online delivery     6929
Is delivering now       6929
Price range             6929
Aggregate rating        6929
Rating color            6929
Rating text             6929
Votes                   6929
Country Name            6929
dtype: int64


### 2. Quantos países únicos estão registrados?

In [43]:
paises = df1.loc[:, 'Country Name'].nunique()
print(f'Existem {paises} paises únicos registrados')

Existem 15 paises únicos registrados


### 3. Quantas cidades únicas estão registradas?

In [44]:
city_unique = df1.loc[:,'City'].nunique()
print(f'Existem {city_unique} cidades únicas registradas')

Existem 125 cidades únicas registradas


### 4. Qual o total de avaliações feitas?

In [25]:
avl_total = df1.loc[:, 'Votes'].sum()
print(f'O total de avaliações feitas é de {avl_total}')

O total de avaliações feitas é de 4194533


### 5. Qual o total de tipos de culinária registrados?

In [27]:
culi_registradas = len(df1.loc[:, 'Cuisines'].unique())
print(f'O total de {culi_registradas} culinárias registradas')

O total de 165 culinárias registradas


In [28]:
cols = ['Average Cost for two', 'Cuisines', 'Aggregate rating', 'City', 'Latitude', 'Longitude']

map = folium.Map()
marker_cluster = MarkerCluster().add_to(map)
for index, location_info in df1.iterrows():
    folium.Marker([location_info['Latitude'],
                 location_info['Longitude']], icon=folium.Icon(color='green')).add_to(marker_cluster)
map

In [29]:
df1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6929 entries, 0 to 6928
Data columns (total 22 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   index                 6929 non-null   int64  
 1   Restaurant ID         6929 non-null   int64  
 2   Restaurant Name       6929 non-null   object 
 3   Country Code          6929 non-null   int64  
 4   City                  6929 non-null   object 
 5   Address               6929 non-null   object 
 6   Locality              6929 non-null   object 
 7   Locality Verbose      6929 non-null   object 
 8   Longitude             6929 non-null   float64
 9   Latitude              6929 non-null   float64
 10  Cuisines              6929 non-null   object 
 11  Average Cost for two  6929 non-null   int64  
 12  Currency              6929 non-null   object 
 13  Has Table booking     6929 non-null   int64  
 14  Has Online delivery   6929 non-null   int64  
 15  Is delivering now    

In [ ]:
print(df.isnull().sum())


In [ ]:
print(df.isna())

In [48]:
df1['Average Cost for two'].unique()

array([    1100,     3100,      800,      700,     1300,     1000,
           1600,     1200,     1500,     1450,     1776,      600,
           2000,     6000,     1800,      850,      500,      400,
           1400,     3000,      100,       50,       55,       80,
            300,       60,      150,       90,       30,       45,
            200,       35,      140,       40,      170,      130,
            250,      120,       70,      180,      160,      230,
             95,      240,      220,       15,      350,        0,
            280,      380,       25,       85,      260,      110,
             96,       65, 25000017,       75,       10,       20,
            275,      105,      165,      115,      175,      650,
            330,      139,       44,      125,      440,      210,
             43,      135,      215,      490,      315,      290,
            340,      270,      755,       38,      225,      190,
            155,      185,      145,      375,      195,      